# City data from Eurostats
We get the data from <http://ec.europa.eu/eurostat/statistics-explained/index.php/Statistics_on_European_cities#Cities_.28Urban_Audit.29>

Looking at the webpage and navigating around, we see an intersting statistics file for "Population on 1 January by age groups and sex - cities and greater cities (urb_cpop1)" at <http://ec.europa.eu/eurostat/web/cities/data/database>

A local version of this statistic is available at ./data/urb_cpop1.tsv (the fileformat seems to be tsv)

### Load necessary libraries

In [1]:
import os # for getting file size
import csv # for handling csv/tsv files

### Check file size of our data

Just to know with what amount of data we have to deal with

In [2]:
urbanAuditFile="./data/urb_cpop1.tsv"
fSize = os.path.getsize(urbanAuditFile)

print('File size of '+urbanAuditFile+' is: '+str(fSize/1024/1024) + ' MBytes')

Looks like a **"bigger"** text file with 4.55MB
* How many lines?

### Inspect the file

**Lets have a look at the first couple of lines**

In [3]:
N=5
with open(urbanAuditFile) as f:
    content=f.read()
    c=0
    for line in content.split("\n"): 
        c+=1
        if c<N:
            print("line "+str(c)+" >> "+line)
print("total lines "+str(c))

In [4]:
#quicker alternative :
with open(urbanAuditFile) as f:
    content=f.readlines()
len(content)

### More "Data sniffing"

This looks like a tab-separated ("\t") file: there are no "," and the formatting indicates some tabs.
The lines seems to have 28 elements (first column as indicator, followed by 27 columns for 2016 - 1990)


That is, the file extension hints at a tabular-separated values (tsv) file, but is this actually the case?

* Inspecting the displayed data may give a hint, e.g., there are no "," or other punctuation marks visible as separators.

* Check explicitly for the presence of a separator, e.g., `\t`

* We could also use the [csv.Sniffer]((https://docs.python.org/3/library/csv.html#csv.Sniffer)) facility for additional validation.

How can the data table be characterized?

* Number of rows?

* Number of columns?

* Is there a header?

In [5]:
with open(urbanAuditFile) as f:
    # a) separator?
    lines = f.readlines()
    print(len([c for c in lines[0] if c == "\t"]) > 1)
    # b) Try to automatically guess "dialect" and delimiter? ... 
    sniffer = csv.Sniffer()
    info1 = sniffer.sniff(lines[1])
    print(info1.delimiter)
    # ...the automatic detection of the delimiter doesn't seem to work all that well :-(
    # ... let's try again to explicitly provide the delimiter:
    info2 = sniffer.sniff(lines[1], delimiters="\t")
    print(info2.delimiter)
    # c) row count?
    print(len(lines))
    # d) column count?
    print((len([c for c in lines[1] if c == "\t"]))+1)

### Parse file as CSV, with 'tab' as delimiter

Now, let's parse this file as CSV files in order to get nice "rows"

In [6]:
with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    c=0 # counter for the parsed line numbers
    N=2 # MAX number of lines we want to output
    for row in csvfile:
        c+=1
        print(row)
        print("Lenght of row "+str(len(row)))
        if c>N:
            break

Ok, that confirms what we thought, tab delimiter and 28 columns.

### How many identifiers? Do we have unique lines?

In [7]:
ind=[]
with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    c=0
    for row in csvfile:
        c+=1
        if c>1: #we skip the first header row
            ind.append(row[0])
uni_ind=set(ind) ## lists can contain duplicates, sets contain only unique elements
print("#unique identifiers "+str(len(uni_ind)))
print("#Rows",c)

Ok 37239 unique indicators and 37240 rows (including header) -> one indicator per row

**Lets inspect some indicators**

In [8]:
for indicator in ind[0:20]:
    print(indicator)#print first 20 indicators

### Observations

Ah ok, this looks like there is a pattern.

Lets try to understand these indicator codes:


We see that there are two types of codes, with "," used to separate the actual indicator and what appears to be the country/city
 * DE1001V,AT

 * DE1001V,AT001C1

The first part ( before the ,) is the indicator variable, the second part refers to the country/city!

BTW, we're in the middle of an exploratory data analysis exercise ;-)

### Different lengths?

In [9]:
_lengths=set([])
for indicator in ind:
    _lengths.add(len(indicator))
print(_lengths)

### Observation

Great, **only two types** of indicator/city codes, the short ones look like country codes, so the longer ones are probably the cities.

## Indicators and their meaning
Browsing through the Eurostats page shows that the indicator codes are listed at "http://dd.eionet.europa.eu/vocabulary/eurostat/indic_ur/" in different formats.

We downloaded the file in CSV to the local file "./data/indic_ur.csv"

In [10]:
indicatorCodesFile="./data/indic_ur.csv"
with open(indicatorCodesFile) as f:
    csvfile = csv.reader(f)
    for i, row in enumerate(csvfile):
        if i<3:
            print(row)
print("Total lines "+str(csvfile.line_num))

Ok 1096 different codes

_ Let us see if our file contains some of the codes _

In [11]:
# check if one of the codes in the first lines appear in this file
with open(indicatorCodesFile) as f:
    csvfile = csv.reader(f)
    for i, row in enumerate(csvfile):
        if 'DE1001V' in row[3]:
            print(row)

Ok, lets keep that in mind, we come back to this later

## City & Country codes
The city codes are available in at "http://dd.eionet.europa.eu/vocabulary/eurostat/cities/", either as [RDF](http://dd.eionet.europa.eu/vocabulary/eurostat/cities/rdf;jsessionid=5AF9B4AF77C5DADF55069F856234E145) or as [CSV](http://dd.eionet.europa.eu/vocabulary/eurostat/cities/csv;jsessionid=5AF9B4AF77C5DADF55069F856234E145)
A local copy of the CSV file is available at "./data/cities.csv" and lists the cities incl their codes and names.

In [12]:
cityCodeFile="./data/cities.csv"
with open(cityCodeFile) as f:
    csvfile = csv.reader(f)
    for i,row in enumerate(csvfile):
        if i<2:
            print(row)
print("Total lines "+str(csvfile.line_num))

Okay, that are a lot of information for each city code and we have 14087 lines, i.e. cities or regions.

Maybe we want to filter the columns for Label (index 1) and Notation (index 3).

In [13]:
with open(cityCodeFile) as f:
    csvfile = csv.reader(f)
    for i,row in enumerate(csvfile):
        # print for the first 5 lines:
        if i<5:
            print(row[1],row[3])

Lets check if they have "Wien":

In [14]:
with open(cityCodeFile) as f:
    csvfile = csv.reader(f)
    for i,row in enumerate(csvfile):
        # filter for a specific city label:
        # ... note that "in" actually matches substrings!
        if 'Wien' in row[1]:
            print(row[1],row[3])

Six different codes for "Wien", go figure ;) (?), actually, we are only interested in the one that has length 15 (remember from above).

### Country Codes

Countries use ISO two-letter codes, e.g. available on [datahub.io](https://datahub.io/de/dataset/iso-3166-1-alpha-2-country-codes/resource/9c3b30dd-f5f3-4bbe-a3cb-d7b2c21d66ce)
 * "CSV":"./data/iso_3166_2_countries.csv" list of countries and country codes.

In [15]:
countryCodeFile="./data/iso_3166_2_countries.csv"
with open(countryCodeFile) as f:
    csvfile = csv.reader(f)
    for i,row in enumerate(csvfile):
        if i<1:
            print(row)
print("Total lines "+str(csvfile.line_num))

Again, lots of columns, but we are mainly interested in the mapping between common name (index 1) and the ISO 2 Letter code (index 10)

In [16]:
with open(countryCodeFile) as f:
    csvfile = csv.reader(f)
    for i,row in enumerate(csvfile):
        if row[1] == 'Austria':
            print(row[1], row[10])

## Thoughts about Merging
At this stage, we would be able to create some dictionaries of
* Indicator -to-> name

* CityCode -to-> city name

* CountryCode -to-> country name

These mappings could be used to provide some more "human friendly" labels in the output...

... Let's keep this in mind, we'll get back to it later.

# Investigating some "interesting" questions
## Which one is the biggest city?

### Lets get the biggest city in 2016

*How can we find the biggest city in 2016?*

1. filter all rows which have
1. the indicator **DE1001V** (=Population on the 1st of January, total) and

2. a city code (length = 15)

2. Parse the population value for the relevant year (2016, i.e. the 2nd column), and
3. store or update the highest population count together with the city name

In [17]:
cityCode=''
cityPopulation=0

#open stream to file in "safe" mode
with open(urbanAuditFile) as f:
    
    #instantiate a CSV Reader with "tab" as value delimiter
    csvfile = csv.reader(f, delimiter="\t")
    
    #iterate over the csv file row-by-row
    for row in csvfile:
        
        #filter for only lines with the 'DE1001V' indicator and cities 
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"):
            if row[1] > cityPopulation: # row[1] is the population of 2016
                cityPopulation = row[1]
                cityCode = row[0].split(",")[1] # split the indicator by "," and take the second part
print("Biggest city: "+cityCode+" with "+str(cityPopulation)+" citizens")

## Observations and Error Explanation

**TypeError: unorderable types: str() > int()** indicates that something is wrong with a data type. In our case, **we compare a numerical value with a character string**

### Solution: Type casting

The **solution is to type cast** the string value to an numerical data type (e.g. int).

As a pre-step, we also remove all leading and trailing whitespaces.
We first remove all leading and ending whitespaces by using the string function **strip()**.
Next, we perform the type cast by using the function ****int( value ) ****

In [18]:
cityCode=''
cityPopulation=0

with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for row in csvfile:
        if 'DE1001V' in row[0] and len(row[0]) > len("DE1001V,AT"): #alternatively len(row[0]) == 15

            ## remove leading and trailing white spaces
            popCount = row[1].strip()
            
            ##type cast
            popCount = int( popCount )
            
            if popCount > cityPopulation: # row[1] is the population of 2016
                cityPopulation=int(popCount)
                cityCode=row[0].split(",")[1] # split the indicator by "," and take the second part
print("Biggest city: "+cityCode+" with "+str(cityPopulation)+" citizens")

## Observation and Error handling

***ValueError: invalid literal for int() with base 10: ':'*** indicates that we tried to type cast a value to int but failed since the value (character) does not belong to the symbols of the numerical value space.


It seems that not all row[1] values are numbers, in fact, missing values are indicated by ":"

### Solution: Filter out rows with cell value == ':'

So lets adapt our filtering approach

In [19]:
cityCode=''
cityPopulation=0

with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for row in csvfile:
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"):

            popCount = row[1].strip()
            
            if popCount != ':':
            
                popCount = int( popCount )
            
                if popCount > cityPopulation: # row[1] is the population of 2016
                    cityPopulation=int(popCount)
                    cityCode=row[0].split(",")[1] # split the indicator by "," and take the second part
print("Biggest city: "+cityCode+" with "+str(cityPopulation)+" citizens")

## Observation and Error Handling

Hmm, clean data looks definitely different!

Seems, like some population values have some additional suffix in form of " d".


### Solution: String manipulation

**ATTENTION: What we should really do now is go back and check what these suffixes mean!**

For now, we will just remove them, by splitting the string at the " " (whitespace) and taking only the former part.

In [20]:
cityCode=''
cityPopulation=0

with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for row in csvfile:
        if 'DE1001V' in row[0] and len(row[0]) > len("DE1001V,AT"):

            popCount = row[1].strip()
            
            ## string manipulation added:
            popCount = popCount.split(" ")[0]
            
            if popCount != ':':
            
                popCount = int( popCount )
                if popCount > cityPopulation: # row[1] is the population of 2016
                    cityPopulation=int(popCount)
                    cityCode=row[0].split(",")[1] # split the indicator by "," and take the second part

print("Biggest city: "+cityCode+" with "+str(cityPopulation)+" citizens")

Ah cool, finally it works and we have as **ES001K1** the biggest city in 2016 (for which we have population values)

Let's try to convert this city code to a more human readable string (or do you know which city it is?)

In [21]:
#Building the cityCode -to-> Label map
cityCodeMap={}
with open(cityCodeFile) as f:
    csvfile = csv.reader(f)
    for i,row in enumerate(csvfile):
        cityCodeMap[row[3]]= row[1]

In [22]:
#lets convert the city code to the label:

print("Biggest city: "+cityCodeMap[cityCode]+" with "+str(cityPopulation)+" citizens")

Better, but somehow strange that Madrid is the biggest city, maybe this is due to the missing values, **lets check for 2015**

In [23]:
cityCode=''
cityPopulation=0
year=2 #2015, helper variable to quickly change years

with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for row in csvfile:
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"):
            popCount=row[year].strip().split(" ")[0]
            if popCount != ":" and int(popCount)>cityPopulation: # row[1] is the population of 2015
                cityPopulation=int(popCount)
                cityCode=row[0].split(",")[1] # split the indicator by "," and take the second part

    print("Biggest city: "+cityCodeMap[cityCode]+" with "+str(cityPopulation)+" citizens")

Ah, ok, looks slightly more realistic, considering that this is Eurostat, Lodon might be the biggest city in Europe.

Looks like "Wikipedia" lists Istanbul (14,657,434) and Moscow (12,330,126) as bigger cities in Europe (source: <https://en.wikipedia.org/wiki/List_of_European_cities_by_population_within_city_limits>)

**Interesting question would be, are these two cities in the dataset or not? How could you figure this out?**

## Trying to interpolate missing values

In [24]:
import numpy as np
import os # for getting file size
import csv # for handling csv/tsv files

urbanAuditFile="./data/urb_cpop1.tsv"

In [25]:
linecounter = 0
with open(urbanAuditFile) as f:
    for line in f:
        print (line)
        linecounter+=1
        if linecounter > 3:
            break

### How much data do we lose if we just delete the lines where the value in 2016 is missing?

In [26]:
right_line_counter = 0
missing_line_counter = 0
with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for i, row in enumerate(csvfile):
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"): # same filter conditition as before
            if row[1].strip() == ":":
                missing_line_counter += 1
            else:
                right_line_counter +=1
                
print (right_line_counter, missing_line_counter)

## Let's just use the most recent value as a proxy for 2016. What are the (most recent) populations per country?

Hmm, well this is just an adaption of our algorithm to find the biggest city in 2016 (which would be the most recent year). However, if the value for 2015 is also missing, we could just take the next most recent value.

Lets try this.

We start by using a dictionary for which the key is the city and the value is another dictionary with the population number for the most recent year.

In addition, we might need to loop over the years to find the most recent year with a existing population value.
Considering that we have a list and operate with indices rather than labels, we want to
* store the first csv row in a field headerRow

* use the headerRow to convert the year index into a Year label

But lets do it step by step

In [27]:
recentCityPopulation={} # key= city , value = {'year': year, 'pop':population}

with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for i, row in enumerate(csvfile):
        if i==0:
            headerRow=row
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"): # same filter conditition as before
            for yearIndex in range (1,27): # this generates all numbers between 1 and 27
                popCount=row[yearIndex].strip().split(" ")[0]
                if popCount != ":" and int(popCount)>0: # check if value exists and we can convert it
                    #ok we have a population value >0, that is hte most recent year, lets store this
                    cityPopulation=int(popCount)
                    cityCode=row[0].split(",")[1]
                    recentCityPopulation[cityCode]={'year':yearIndex,'pop': cityPopulation}
                    # important: break when you found the first actual value (which means you'll keep the most recent year)
                    break
                    
print(recentCityPopulation)

Ok, doesn't look "too bad", but hard to read for a human and we do not want to present the values like that.

Let's fix it! We can
* convert the cityCode to City labels and

* replace the yearIndices with the respective column headers, i.e., year labels.

In [28]:
# Clear the dictionary again:
recentCityPopulation={} # key= city , value = {'year': year, 'pop':population}

## a quick trick to be able to convert the yearIndex to its label
headerRow=[]
with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for i, row in enumerate(csvfile):
        if i==0:
            headerRow=row
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"): # same filter conditition as before
            for yearIndex in range (1,27): # this generates all numbers between 1 and 27
                popCount=row[yearIndex].strip().split(" ")[0]
                if popCount != ":" and int(popCount)>0: # check if value exists and we can convert it
                    #ok we have a population value >0, that is hte most recent year, lets store this
                    cityPopulation=int(popCount)
                    cityCode=row[0].split(",")[1]
                    cityLabel=cityCodeMap[cityCode] # lets just merge the mapping from city code to label in this code
                    recentCityPopulation[cityLabel]={'year':headerRow[yearIndex],'pop': cityPopulation} # we also convert hte year index to the year label
                    break
## lets fix also the printing 
print("Number of cities: "+str(len(recentCityPopulation.keys())))
for city, pop in recentCityPopulation.items():
    print("  "+city+":"+str(pop['pop'])+" in "+str(pop['year']))

## Observations
* We have in total 995 cities with a population value

In [29]:
years=[]
for city, pop in recentCityPopulation.items():
    years.append(pop['year'])
print("oldest value in ", min(years))
print("newest value in ", max(years))

In [30]:
import numpy as np

pop_2016 = {}

with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    
    # The first row contains the years, from the second field onwards... 
    # which we convert to a list of integers:
    years = list(map(int, next(csvfile)[1:]))
    #print(years)
    
    for row in csvfile:
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"): # same filter conditition as before

            if row[1].strip() == ':':
                pop_values = []
                for x, y in enumerate(row[2:]):
                    pop_value = y.split(' ')[0]
                    if pop_value != ':':
                        pop_values.append(float(pop_value))
                pop_2016[row[0]] = np.mean(pop_values)
            else: 
                pop_2016[row[0]] = float(row[1].split(' ')[0])
                
#print(pop_2016.keys())             
#print(pop_2016['DE1001V,BE001C1'])

What is the largest city based on the mean interpolation data?

In [31]:
max(pop_2016, key=pop_2016.get)
print(pop_2016['DE1001V,TR012C1'])

# You can tell that it was actually predicted from the mean, beucase of .5 ending. 
# This is Turkey, Istambul.

The mean interpolation can be an easy fix but in this case we know that the values are mostly growing over time, so simply using the last known value might even be better.

In the case of Istambul for example, we might have underestimated the population since it has been growing in the past 20 years. Let's have a look at all the values:

In [32]:
with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    
    for row in csvfile:
        if 'DE1001V,TR012C1' in row[0] :
            print(row)

Actually, rather than an underestimation, it just looks like a quite bad guess since it is based on only two existing values.

### Trying to interpolate missing values with numpy's built in interp function

In [33]:
import csv # for handling csv/tsv files
interpolated_dict={}
with open('./data/urb_cpop1.tsv') as f:
    csvfile = csv.reader(f,delimiter="\t")
    
    # The first row contains the years, from the second field onwards... 
    # which we convert to a list of integers:
    years = list(map(int, next(csvfile)[1:]))

    # Now we process the second line onwards to populate the dictionary:    
    for row in csvfile:
        xp=[]
        fp=[]
        for x,y in enumerate(row[1:]):
            if y[0] != ":":
                xp.insert(0,2016-x)
                fp.insert(0,float(y.split(' ')[0]))
        interpolated_dict[row[0]] = dict(zip(years, np.interp(years,xp,fp)))

In [34]:
print(len(interpolated_dict))

careful, the dictionary contains 37239 entries, **do not print**

In [35]:
print(interpolated_dict["DE1001V,AT"])

In [36]:
#Building the cityCode -to-> Label map
cityCodeFile="./data/cities.csv"
cityCodeMap={}
with open(cityCodeFile) as f:
    csvfile = csv.reader(f)
    for i,row in enumerate(csvfile):
        cityCodeMap[row[3]]= row[1]

### Next, we create a dictionary with the most recent population values (recentCityPopulation). Then we can merge this dictionary with the interpolated dictionary to have all values for 2016.

In [37]:
# Create the most recent population dictionary again:
recentCityPopulation={} # key= city , value = {'year': year, 'pop':population}

## a quick trick to be able to convert the yearIndex to its label
headerRow=[]
with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for i, row in enumerate(csvfile):
        if i==0:
            headerRow=row
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"): # same filter conditition as before
            for yearIndex in range (1,27): # this generates all numbers between 1 and 27
                popCount=row[yearIndex].strip().split(" ")[0]
                if popCount != ":" and int(popCount)>0: # check if value exists and we can convert it
                    #ok we have a population value >0, that is hte most recent year, lets store this
                    cityPopulation=int(popCount)
                    cityCode=row[0].split(",")[1]
                    cityLabel=cityCodeMap[cityCode] # lets just merge the mapping from city code to label in this code
                    recentCityPopulation[cityLabel]={'year':headerRow[yearIndex],'pop': cityPopulation} # we also convert hte year index to the year label
                    break
## lets fix also the printing 
print("Number of cities: "+str(len(recentCityPopulation.keys())))
for city, pop in recentCityPopulation.items():
    print("  "+city+":"+str(pop['pop'])+" in "+str(pop['year']))

In [38]:
# Add the values from the interpolated dictionary where values are missing for 2016. 

recentCityPopulation={} # key= city , value = {'year': year, 'pop':population}

## a quick trick to be able to convert the yearIndex to its label
headerRow=[]
with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for i, row in enumerate(csvfile):
        if i==0:
            headerRow=row
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"): # same filter conditition as before
            for yearIndex in range (1,27): # this generates all numbers between 1 and 27
                popCount=row[yearIndex].strip().split(" ")[0]
                
                if popCount == ":" or int(popCount)==0:
                    #no population count for this city/country in the relevant year
                    
                    #check if the indicator code is in the interpolated map
                    if row[0] in interpolated_dict:
                        year=2016-yearIndex
                        if year in interpolated_dict[row[0]]:
                            cityPopulation = interpolated_dict[row[0]][year]
                            cityCode=row[0].split(",")[1]
                            cityLabel=cityCodeMap[cityCode] # lets just merge the mapping from city code to label in this code
                            recentCityPopulation[cityLabel]={'year':headerRow[yearIndex],'pop': cityPopulation} # we also convert the year index to the year label
                            break
                else:
                    #ok we have a population value >0, that is the most recent year, lets store this
                    cityPopulation=int(popCount)
                    cityCode=row[0].split(",")[1]
                    cityLabel=cityCodeMap[cityCode] # lets just merge the mapping from city code to label in this code
                    recentCityPopulation[cityLabel]={'year':headerRow[yearIndex],'pop': cityPopulation} # we also convert hte year index to the year label
                    break

Check whether it worked. If the most recent values are all 2016, we know it worked!

In [39]:
years=[]
for city, pop in recentCityPopulation.items():
    years.append(pop['year'])
    print("oldest value in ", city, min(years), pop)
    print("newest value in ", city, max(years),  pop)

# Merging Datasets & duplicate detection

**Question:** What is the (most recent) population number of London?

Two datasets:
* "UrbanAudit": "(./data/urb_cpop1.csv)" - indicator DE1001V is the total population, names of cities are in a separate file "cities.csv": "(./data/cities.csv)"

* "UNData": "(./data/UNdata_Export_20171029_111415830.csv)" - total population is indicated by the values
    "Total","Both Sexes"
  in the 3rd and 4th column, city name is in the 5th column, some city names are in upper case. The source year is in the 9th column and the actual population number is in the 10th column.

Let's try to get the data into a unique format into **one** dictionary. For the EU data we have done this already, let's take  the same code and slightly adapt it:

In [40]:
import csv # for handling csv/tsv files

# The two files containing information about cities
urbanAuditFile="./data/urb_cpop1.tsv"
cityCodeFile="./data/cities.csv"

#Building the cityCode to Label map
cityCodeMap={}
with open(cityCodeFile) as f:
    csvfile = csv.reader(f)
    for i,row in enumerate(csvfile):
        cityCodeMap[row[3]]= row[1]
#cityCodeMap

In [41]:
# the dictionary we plan to build will look like this
# key= cityname-lowercase-ISO-20letter-country code, 
# value = {'year': year, 'pop':population}
recentCityPopulationEU={} 


## a quick trick to be able to convert the yearIndex to its label
## We know this snippet from last time... now we will use the lower-case for the labels, in order 
## to avoid confusion with upper and lower case names:

headerRow=[]
with open(urbanAuditFile) as f:
    csvfile = csv.reader(f, delimiter="\t")
    for i, row in enumerate(csvfile):
        #first row becomes the header
        if i==0:
            headerRow=row
        if 'DE1001V' in row[0] and len(row[0])> len("DE1001V,AT"): # same filter conditition as before
            for yearIndex in range (1,27): # this generates all numbers between 1 and 27
                popCount=row[yearIndex].strip().split(" ")[0]
                if popCount != ":" and int(popCount)>0: # check if value exists and we can convert it
                    #ok we have a population value >0, that is the most recent year, lets store this
                    # now create the values we want to store in the dictionary: population count as an integer, 
                    # and the name of the city, using the dictionary we preciously defined and the city code
                    cityPopulation=int(popCount)
                    cityCode=row[0].split(",")[1]
                    cityLabel=cityCodeMap[cityCode].lower() # lets just merge the mapping from city code to label in this code
                    
                    # small modification, we also add the 2 letter country code in uppercase to the key (we will need this later:
                    cityLabelCC = cityLabel + (row[0].split(',')[1][0:2])  
                    recentCityPopulationEU[cityLabelCC]={'year': headerRow[yearIndex],'pop': cityPopulation, } # we also convert the year index to the year label
                    break # we break the loop at the first year that is not missing, to get the most recent pop. count

### This is how we can interact with this dicionaty now:

In [42]:
print("Number of cities: "+str(len(recentCityPopulationEU.keys())))

In [43]:
for city, pop in recentCityPopulationEU.items():
    print("  "+city+":"+str(pop['pop'])+" in "+str(pop['year']))

In [44]:
print(recentCityPopulationEU['wienAT'])

In [45]:
print("Population count of Vienna: ", recentCityPopulationEU['wienAT']["pop"])

### UNData Inspection

Now let's look into the UN Data file:

In [46]:
undatafile = 'data/UNdata_Export_20171029_111415830.csv'

recentCityPopulationUN={}

N=10
with open(undatafile) as f:
    csvfile = csv.reader(f)  
    c=0
    for row in csvfile:
        c=c+1
        print (row)
        if c >N:
            break

Our goal is to build a similar dictionaty to the previous.
In this process, we will try to cautiously check for duplicates. To this end, for the moment, we also store the original rows in the dictionary:

### Build same dictionary

* key= cityCountryISO2

* value is again a dictionary

  * 'year' = year

  * 'pop = population


**Duplication check**
Check if a new key is already existing in the dictionary

In [47]:
undatafile = 'data/UNdata_Export_20171029_111415830.csv'

recentCityPopulationUN={}

with open(undatafile) as f:
    csvfile = csv.reader(f)

    for row in csvfile:
        # filter for the lines that are relevant for us
        if len(row) > 10 and row[2] == "Total" and row[3] == "Both Sexes":
            cityLabel = row[4].lower()
            # The if part covers dedectung duplicates:
            if cityLabel in recentCityPopulationUN and recentCityPopulationUN[cityLabel]['year'] <= row[8]:
                if recentCityPopulationUN[cityLabel]['year'] == row[8]:
                    print("Duplicate found!\n" + str(row) + "\n" + str(recentCityPopulationUN[cityLabel]['row']) + "\n")
                # implicit missing 'else' branch: if the year was older than the one already sotred, then ignore this line.
            else:
                recentCityPopulationUN[cityLabel] = {'year': row[8],'pop': float(row[9]), 'row' : row} 
                
# if the year is larger than a year we already stored, we want to overwrite the dictionary and store that element 
# (since we want the most recent one). If the year is smaller, we don't want to do anything. If it's the same year, 
# then we found a duplicate!

Oops! This produces a lot of duplicates, e.g.:

    Duplicate found!
    ['Åland Islands', '2008', 'Total', 'Both Sexes', 'MARIEHAMN', 'City proper', 'Estimate - de jure', 'Final figure, complete', '2009', '10954', '1']
    ['Åland Islands', '2009', 'Total', 'Both Sexes', 'MARIEHAMN', 'City proper', 'Estimate - de jure', 'Final figure, complete', '2009', '11064', '1']

What this tells us it that different *reported* years (2nd column) in the data seem to have the same source year (9th column).

**We can eliminate these duplicates easily by just referring to the reported year instead of the source year**

In [48]:
recentCityPopulationUN={}

with open(undatafile) as f:
    csvfile = csv.reader(f)

    for row in csvfile:
        if len(row) > 10 and row[2] == "Total" and row[3] == "Both Sexes":
            cityLabel = row[4].lower()
            # Note that we changed to row[1] here:
            if cityLabel in recentCityPopulationUN and recentCityPopulationUN[cityLabel]['year'] <= row[1]:
                if recentCityPopulationUN[cityLabel]['year'] == row[1]:
                    print("Duplicate found!\n" + str(row) + "\n" + str(recentCityPopulationUN[cityLabel]['row']) + "\n"  )
            else:
                recentCityPopulationUN[cityLabel] = {'year': row[1],'pop': float(row[9]),'row' : row}

Ouch! Again there are many duplicates in the data... E.g.:

    Duplicate found!
    ['Argentina', '1991', 'Total', 'Both Sexes', 'BUENOS AIRES', 'Urban agglomeration', 'Census - de facto - complete tabulation', 'Final figure, complete', '1991', '11298030', '']
    ['Argentina', '1991', 'Total', 'Both Sexes', 'BUENOS AIRES', 'City proper', 'Census - de facto - complete tabulation', 'Final figure, complete', '1991', '2965403', '']

**These seem to indicate that the UN Dataset have also the same city name appearing in different city types**: the "Urban agglomeration" area or the "City proper" area.

We could fix the code by only including one type, for example by addign this to the filter: and row[5] == "Urban agglomeration". This would have the upside that we only compare the same type of counts. On the other hand this might lead to losing data in the cases where we only have information about city proper.

So let's fix the code to prefer the numbers given for the "Urban agglomeration", in such cases:

In [49]:
recentCityPopulationUN={}

with open(undatafile) as f:
    csvfile = csv.reader(f)

    for row in csvfile:
        if len(row) > 10 and row[2] == "Total" and row[3] == "Both Sexes":
            cityLabel = row[4].lower()
            if (cityLabel in recentCityPopulationUN and recentCityPopulationUN[cityLabel]['year'] <= row[1] and 
                # Adding another condition: only report a duplicate when the new city type is not "City Proper" and the to be replaced type is not "Urban agglomeration" 
                not (row[5] == "Urban agglomeration" and  
                     recentCityPopulationUN[cityLabel]['row'][5] == "City proper")):
                  if recentCityPopulationUN[cityLabel]['year'] == row[1]:
                    print("Duplicate found!\n" + str(row) + "\n" + str(recentCityPopulationUN[cityLabel]['row']) + "\n"  )
            else:
                recentCityPopulationUN[cityLabel] = {'year': row[1],'pop': float(row[9]),'row' : row}

Hmmm, again duplicates, this time of the form:

    Duplicate found!
    ['Austria', '2011', 'Total', 'Both Sexes', 'Bregenz', 'City proper', 'Estimate - de jure', 'Final figure, complete', '2011', '27784', '18']
    ['Austria', '2011', 'Total', 'Both Sexes', 'Bregenz', 'City proper', 'Census - de jure - complete tabulation', 'Final figure, complete', '2012', '27831', '']

Now these indicate that there are different measure methods... here we could opt to overwrite estimates:

In [50]:
recentCityPopulationUN={}

with open(undatafile) as f:
    csvfile = csv.reader(f)

    for row in csvfile:
        if len(row) > 10 and row[2] == "Total" and row[3] == "Both Sexes":
            cityLabel = row[4].lower()
            if (cityLabel in recentCityPopulationUN and recentCityPopulationUN[cityLabel]['year'] <= row[1] and 
                # Adding another condition: only report a duplicate when the existing city type is not "City Proper" and the to be replaced type is not "Urban agglomeration" 
                not (row[5] == "Urban agglomeration" and  
                     recentCityPopulationUN[cityLabel]['row'][5] == "City proper") and
                # Adding another condition: only report a duplicate when the existing method not is "Estimate ..." and new one is something else. 
                not (row[6][0:7] != "Estimate" and  
                     recentCityPopulationUN[cityLabel]['row'][5][0:7] == "Estimate")):
                if (recentCityPopulationUN[cityLabel]['year'] == row[1] and
                    row[6][0:7] != "Estimate" and  
                     recentCityPopulationUN[cityLabel]['row'][5][0:7] == "Estimate"):
                    print("Duplicate found!\n" + str(row) + "\n" + str(recentCityPopulationUN[cityLabel]['row']) + "\n"  )

            else:
                recentCityPopulationUN[cityLabel] = {'year': row[1],'pop': float(row[9]),'row' : row}

## Did we really resolve all duplicates now?

Have we really resolved all duplicates now?

What about cities with the same names in different countries? Let's check whether such cases exist in the UN dataset!

In [51]:
with open(undatafile) as f:
    csvfile = csv.reader(f)
    
    city_country_dict = {}

    # we want to build up a dictionary to check whether there are cities with the same 
    # name but different countries in our dataset
    # i.e. key = cityname value = country 

    for row in csvfile:
        if len(row) > 10 and row[2] == "Total" and row[3] == "Both Sexes":
            cityLabel = row[4].lower()
            country = row[0].lower()
            if  (cityLabel in city_country_dict and
                 city_country_dict[cityLabel] != country):
                print("Different countries found for City: '" + cityLabel + "': " + country + " vs " + city_country_dict[cityLabel]) 
            else:
                city_country_dict[cityLabel] = country

Too bad, e.g.:

    Different countries found for City: london: united kingdom of great britain and northern ireland vs canada

we can fix this by adding the country code to the city label, remember, we did that before for the Eurostat cities, but here it is more difficult, since we need to lookup the country codes in the ISO file (to arrive at the same lables we had in the EU file!

### Country code in ISO2 format

Let's first build a dictionary of countrycodes... We have seen that last above:

In [52]:
countryCodeFile = './data/iso_3166_2_countries.csv'

countryCodeDict = {}

with open(countryCodeFile) as f:
    csvfile = csv.reader(f)
    for row in csvfile:
        countryCodeDict[row[1]] = row[10]

Now let's use this dictionary to modify the example code from above to rebuild the UN city population dictionary:

In [53]:
recentCityPopulationUN={}

with open(undatafile) as f:
    csvfile = csv.reader(f)

    for row in csvfile:
        if len(row) > 10 and row[2] == "Total" and row[3] == "Both Sexes":
            # This is the only modification: we add a lookup for the countryname to append the 
            # countrycode to the city label: 
            cityLabel = row[4].lower() + countryCodeDict[row[0]] 
            if (cityLabel in recentCityPopulationUN and recentCityPopulationUN[cityLabel]['year'] <= row[1] and 
                not (row[5] == "Urban agglomeration" and  
                     recentCityPopulationUN[cityLabel]['row'][5] == "City proper") and
                not (row[6][0:7] != "Estimate" and  
                     recentCityPopulationUN[cityLabel]['row'][5][0:7] == "Estimate")):
                if (recentCityPopulationUN[cityLabel]['year'] == row[1] and
                    row[6][0:7] != "Estimate" and  
                     recentCityPopulationUN[cityLabel]['row'][5][0:7] == "Estimate"):
                    print("Duplicate found!\n" + str(row) + "\n" + str(recentCityPopulationUN[cityLabel]['row']) + "\n"  )
            else:
                recentCityPopulationUN[cityLabel] = {'year': row[1],'pop': float(row[9]),'row' : row}

Too bad, that doesn't work, since some countries have different names in the countries file from ISO and from the UN.
We would probably need additional data to resolve these... **for the moment, we will simply ignore those countries**.

In [54]:
recentCityPopulationUN={}

with open(undatafile) as f:
    csvfile = csv.reader(f)

    for row in csvfile:
        if len(row) > 10 and row[2] == "Total" and row[3] == "Both Sexes":
            
            ### the 3 new lines ###
            if row[0] in countryCodeDict:
                cityLabel = row[4].lower() + countryCodeDict[row[0]]
            else: continue # continue jumps over this row and continues in the next iteration of the for loop 
            
            if (cityLabel in recentCityPopulationUN and recentCityPopulationUN[cityLabel]['year'] <= row[1] and 
                # Adding another condition: only report a duplicate when the existing city type is not "City Proper" and the to be replaced type is not "Urban agglomeration" 
                not (row[5] == "Urban agglomeration" and  
                     recentCityPopulationUN[cityLabel]['row'][5] == "City proper") and
                # Adding another condition: only report a duplicate when the existing method not is "Estimate ..." and new one is something else. 
                not (row[6][0:7] != "Estimate" and  
                     recentCityPopulationUN[cityLabel]['row'][5][0:7] == "Estimate")):
                if (recentCityPopulationUN[cityLabel]['year'] == row[1] and
                    row[6][0:7] != "Estimate" and  
                     recentCityPopulationUN[cityLabel]['row'][5][0:7] == "Estimate"):
                    print("Duplicate found!\n" + str(row) + "\n" + str(recentCityPopulationUN[cityLabel]['row']) + "\n"  )
            else:
                recentCityPopulationUN[cityLabel] = {'year': row[1],'pop': float(row[9]),'row' : row}

Now we should be ready to merge the two datasets! our strategy is to build a joint dictionary `recentCityPopulation`,
where we collect the average pop `popAvg`, `popEU` and `popUN`

In [55]:
recentCityPopulation = {}

for key in recentCityPopulationUN:
    recentCityPopulation[key] = {'popUN': recentCityPopulationUN[key]['pop'],
                                 'pop' : recentCityPopulationUN[key]['pop'] }


for key in recentCityPopulationEU:
    if key in recentCityPopulation:
        recentCityPopulation[key]['popEU'] = recentCityPopulationEU[key]['pop'] 
        recentCityPopulation[key]['pop'] = (recentCityPopulation[key]['pop'] + recentCityPopulation[key]['popEU'])/2 
    else: 
        recentCityPopulation[key] = {'popEU': recentCityPopulationEU[key]['pop'],
                                     'pop' : recentCityPopulationEU[key]['pop'] }
# An example:        
print(recentCityPopulation['wienAT'])